In [1]:
import numpy as np
import torch
from PIL import Image
import cv2
import os
import open3d
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
import time
from torch.optim import lr_scheduler
from torch.utils.data import DataLoader
from collections import defaultdict
import random
import mano
import trimesh
from pytorch3d.structures import Meshes
import open3d as o3d
import pickle
import json
from utils import utils
from utils import utils_loss
from pytorch3d.loss import mesh_laplacian_smoothing
from scipy.linalg import orthogonal_procrustes
torch.cuda.set_device(5)

Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.


In [2]:
def align_w_scale(mtx1, mtx2, return_trafo=False):
    """ Align the predicted entity in some optimality sense with the ground truth. """
    # center
    t1 = mtx1.mean(0)
    t2 = mtx2.mean(0)
    mtx1_t = mtx1 - t1
    mtx2_t = mtx2 - t2

    # scale
    #s1 = np.linalg.norm(mtx1_t) + 1e-8
    mtx1_t# /= s1
    #s2 = np.linalg.norm(mtx2_t) + 1e-8
    mtx2_t# /= s2

    # orth alignment
    R, s = orthogonal_procrustes(mtx1_t, mtx2_t)

    # apply trafos to the second matrix
    mtx2_t = np.dot(mtx2_t, R.T) #* s
    mtx2_t = mtx2_t+ t1# * s1 + t1
    if return_trafo:
        return R, s, s1, t1 - t2
    else:
        return mtx2_t

In [3]:
object_path='/data/zz/HMDO/sequence01/object_mesh/'
object_mesh = trimesh.load(os.path.join(object_path, '0071.ply'))#.vertices
object_mesh_org = trimesh.load("/data/zz/HMDO/template_models/01_mouse.ply")#.vertices
obj_mesh_soft =  trimesh.load(os.path.join(object_path, '0071.ply'))#.vertices
object_mesh_org_org = trimesh.load("/data/zz/HMDO/template_models/01_mouse.ply")

with open(os.path.join("/data/zz/HMDO/sequence01/hand_annotation/","0071"+'.txt'), 'r') as file:
    content = file.read()
numbers = content.split(',')
with open(os.path.join("/data/zz/HMDO/sequence01/object_annotation/","0071"+'.txt'), 'r') as file:
    object_tran = file.read()
object_trans = object_tran.split(',')
object_rot = []
for i in range(0,len(object_trans)-1):
    object_rot.append(float(object_trans[i]))
print(object_rot)
print(len(numbers))
scale=float(numbers[0])
#hand_vertices=hand_vertices/scale
object_mesh.vertices=object_mesh.vertices/scale
object_mesh_org.vertices  = object_mesh_org.vertices /scale
obj_mesh_soft.vertices  = obj_mesh_soft.vertices/scale
object_mesh_org_org.vertices  = object_mesh_org_org.vertices/scale

[-0.116853, 0.373032, -0.271102, -26.5511, 5.80104, -678.588]
53


In [4]:

object_mesh.vertices = align_w_scale(object_mesh_org.vertices,object_mesh.vertices)



meshes = [object_mesh_org,object_mesh]
trimesh.Scene(meshes).show()    


In [5]:

#obj_mesh_soft = object_mesh
obj_mesh_soft.vertices = object_mesh_org.vertices - object_mesh.vertices
mean_move =[0,0,0]
#mean_move[0] = (obj_mesh_soft.vertices*(obj_mesh_soft.vertices<3e-3)).sum(0)/(obj_mesh_soft.vertices<3e-3).sum(0)\
d =  torch.norm(torch.tensor(obj_mesh_soft.vertices), dim=1, keepdim=True)
mean_move = (obj_mesh_soft.vertices*np.array(((d < 3e-3) & (d > 3e-4)))).sum(0)/np.array(((d < 3e-3) & (d > 3e-4))).sum()

print(mean_move)
object_mesh.vertices = object_mesh.vertices + mean_move
obj_mesh_soft.vertices = object_mesh_org.vertices - object_mesh.vertices
print((d>3e-4).sum())
obj_mesh_soft.vertices = obj_mesh_soft.vertices#*np.array((d>3e-4))
meshes = [obj_mesh_soft]
trimesh.Scene(meshes).show()  



[ 9.33985432e-05 -2.99198457e-04 -7.95971889e-05]
tensor(5923)


In [6]:
object_mesh_org.vertices = object_mesh_org.vertices-obj_mesh_soft.vertices

#object_mesh_org.vertices = object_mesh.vertices
meshes = [object_mesh_org]
vertices = torch.tensor(object_mesh_org.vertices, dtype=torch.float32)
faces = torch.tensor(object_mesh_org.faces, dtype=torch.int64)
pytorch3d_mesh = Meshes(verts=[vertices], faces=[faces])
loss_smoothing_tmp = mesh_laplacian_smoothing(pytorch3d_mesh, method='uniform')
print(loss_smoothing_tmp)
trimesh.Scene(meshes).show()  

tensor(0.0004)


In [7]:

with torch.no_grad():
        rh_mano = mano.load(model_path='./models/mano/MANO_RIGHT.pkl',
                            model_type='mano',
                            use_pca=False,
                            num_pca_comps=51,
                            batch_size=1,
                            flat_hand_mean=True)
device = torch.device("cpu")

rh_faces = torch.from_numpy(rh_mano.faces.astype(np.int32)).view(1, -1, 3)  # [1, 1538, 3], face triangle indexes
rh_mano.eval()
recon_param = torch.zeros((1, 61)).to(device)
number = []
for i in range(1,len(numbers)-1):
    #print(numbers[i])
    number.append(float(numbers[i]))
content = torch.tensor(number).unsqueeze(0)
print(content.size())
recon_param[:, :10] = torch.tensor([10,10,10,10,10,10,10,10,10,10]).float()
recon_mano = rh_mano(betas=recon_param[:, :10], global_orient=content[:,3:6],
                                     hand_pose=content[:,6:51], transl=content[:, 0:3])
recon_xyz = recon_mano.vertices.to(device)

print(recon_xyz.size())
print(rh_faces.size())
hand_mesh = trimesh.Trimesh(vertices=recon_xyz.squeeze(0).detach().cpu().numpy(), faces=rh_faces.detach().cpu().numpy().reshape((-1, 3)),face_colors=[int(0.85882353*255), int(0.74117647*255), int(0.65098039*255)])
object_mesh = trimesh.load(os.path.join(object_path, '0071.ply'))#.vertices
object_mesh.vertices=object_mesh.vertices/scale
meshes=[hand_mesh,object_mesh]

trimesh.Scene(meshes).show()

torch.Size([1, 51])
torch.Size([1, 778, 3])
torch.Size([1, 1538, 3])


In [8]:
file = '0071.ply'
sid = "01"
hand_mesh_r = trimesh.load(os.path.join("/data/zz/HMDO/sequence"+sid+"/hand_mesh/", file))
hand_mesh_r.vertices = hand_mesh_r.vertices/scale
meshes=[hand_mesh,hand_mesh_r,object_mesh]
trimesh.Scene(meshes).show()

In [9]:
def transform_obj_verts(verts, trans, cam_extr):
    #verts = verts * 1000
    hom_verts =verts# np.concatenate([verts, np.ones([verts.shape[0], 1])], axis=1)
    trans_verts = trans.dot(hom_verts.T).T
    trans_verts = cam_extr.dot(trans_verts.transpose()).transpose()[:, :3]
    return trans_verts

In [11]:
rot_angles = object_rot[0:3]
theta_x, theta_y, theta_z = rot_angles[0], rot_angles[1], rot_angles[2]
Rx = np.array([[1, 0, 0], [0, np.cos(theta_x), -np.sin(theta_x)], [0, -np.sin(theta_x), np.cos(theta_x)]])
Ry = np.array([[np.cos(theta_y), 0, -np.sin(theta_y)], [0, 1, 0], [np.sin(theta_y), 0, np.cos(theta_y)]])
Rz = np.array([[np.cos(theta_z), np.sin(theta_z), 0], [-np.sin(theta_z), np.cos(theta_z), 0], [0, 0, 1]])
rot = Rx @ Ry @ Rz
object_mesh_org_org.vertices =(object_mesh_org_org.vertices*scale)@ np.array(rot)
object_mesh_org_org.vertices =object_mesh_org_org.vertices/scale +np.array([object_rot[3:6]])/scale

In [12]:

meshes=[object_mesh_org_org,object_mesh]
trimesh.Scene(meshes).show()